# Imports

In [1]:
import requests
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import calendar
from shapely import wkb
from statsmodels.tsa.seasonal import MSTL
from plotly.subplots import make_subplots

# Fetch data from api

In [198]:
def fetch_data(
    dataset_id: str = "comptage-multimodal-comptages",
    export_format: str = "parquet",
    save_path: str = "../data/01_raw/comptage-multimodal-comptages.parquet",
) -> None:
    """
    Download the multimodal counting data (bikes + scooters) for Boulevard Sébastopol
    from the OpenDataSoft API in Parquet format and save it locally.
    """
    # Build the endpoint URL
    url = (
        f"https://parisdata.opendatasoft.com/api/explore/v2.1/catalog/"
        f"datasets/{dataset_id}/exports/{export_format}"
    )

    # Query parameters: filter to both bike and scooter modes on the two Sebastopol counters
    params = {
        "refine": [
            "mode:Trottinettes + vélos",
            "mode:Trottinettes",
            "mode:Vélos",
            "label:CF1461_113 boulevard de Sébastopol",
            "label:CF0001_9 boulevard de Sébastopol",
        ],
        "timezone": "UTC",
        "limit": -1,
        "parquet_compression": "snappy",
    }

    # Send request and save the response content to disk
    response = requests.get(url, params=params)
    response.raise_for_status()

    with open(save_path, "wb") as f:
        f.write(response.content)

    print(f"File downloaded and saved to: {save_path}")


In [199]:
fetch_data()

File downloaded and saved to: ../data/01_raw/comptage-multimodal-comptages.parquet


# Load data from filesystem

In [200]:
df = pd.read_parquet(
    "../data/01_raw/comptage-multimodal-comptages.parquet", engine="pyarrow"
)

# Inspect data

In [201]:
# Show the first few rows of the DataFrame
display(df.head())
# Show df info
print(df.info())

# Show unique values for key columns
for x in [
    "id_site",
    "label",
    "sens",
    "id_trajectoire",
    "trajectoire",
    "coordonnees_geo",
]:
    print(f"Unique values in {x}: {df[x].unique()} Total: {df[x].nunique()}")

# Check for missing values
print(df.isna().sum())

id_trajectoire id_site                             label  \
0   10030_4 -> 2   10030  CF0001_9 boulevard de Sébastopol   
1   10030_2 -> 1   10030  CF0001_9 boulevard de Sébastopol   
2   10030_3 -> 2   10030  CF0001_9 boulevard de Sébastopol   
3   10030_1 -> 1   10030  CF0001_9 boulevard de Sébastopol   
4   10030_2 -> 1   10030  CF0001_9 boulevard de Sébastopol   

                          t          mode  nb_usagers  \
0 2024-03-15 03:00:00+00:00  Trottinettes           4   
1 2024-07-24 09:00:00+00:00         Vélos          12   
2 2024-06-03 05:00:00+00:00  Trottinettes          32   
3 2024-06-01 17:00:00+00:00         Vélos          26   
4 2023-11-10 18:00:00+00:00         Vélos          16   

                           voie sens trajectoire  \
0                Piste cyclable  N-S      4 -> 2   
1  Voie de circulation générale  S-N      2 -> 1   
2                Piste cyclable  S-N      3 -> 2   
3  Voie de circulation générale  S-N      1 -> 1   
4  Voie de circulation générale  S-N      2 -> 1   

                                     coordonnees_geo  
0  b'\x01\x01\x00\x00\x00\x01\xa5\xa1F!\xc9\x02@\...  
1  b'\x01\x01\x00\x00\x00\x01\xa5\xa1F!\xc9\x02@\...  
2  b'\x01\x01\x00\x00\x00\x01\xa5\xa1F!\xc9\x02@\...  
3  b'\x01\x01\x00\x00\x00\x01\xa5\xa1F!\xc9\x02@\...  
4  b'\x01\x01\x00\x00\x00\x01\xa5\xa1F!\xc9\x02@\...

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 263173 entries, 0 to 263172
Data columns (total 10 columns):
 #   Column           Non-Null Count   Dtype              
---  ------           --------------   -----              
 0   id_trajectoire   263173 non-null  object             
 1   id_site          263173 non-null  object             
 2   label            263173 non-null  object             
 3   t                263173 non-null  datetime64[ms, UTC]
 4   mode             263173 non-null  object             
 5   nb_usagers       263173 non-null  int64              
 6   voie             263173 non-null  object             
 7   sens             263173 non-null  object             
 8   trajectoire      263173 non-null  object             
 9   coordonnees_geo  263173 non-null  object             
dtypes: datetime64[ms, UTC](1), int64(1), object(8)
memory usage: 20.1+ MB
None
Unique values in id_site: ['10030' '10180'] Total: 2
Unique values in label: ['CF0001_9 boulevard de 

# Basic transformations

In [202]:
def preprocess_df(df: pd.DataFrame) -> pd.DataFrame:
    """
    Convert the 't' column to Europe/Paris timezone, parse WKB coordinates into latitude and longitude,
    and remove raw geometry columns.
    """
    df = df.copy()
    # 1) Convert timestamp to Europe/Paris timezone
    df["t_paris"] = df["t"].dt.tz_convert("Europe/Paris")

    # add date column for easier filtering
    df["date"] = df["t_paris"].dt.strftime("%Y-%m-%d")

    # 2) Parse WKB bytes into Shapely geometry
    df["geometry"] = df["coordonnees_geo"].apply(wkb.loads)

    # 3) Extract longitude (x) and latitude (y)
    df["lon"] = df["geometry"].apply(lambda point: point.x)
    df["lat"] = df["geometry"].apply(lambda point: point.y)

    # 4) Drop raw geometry columns
    df.drop(columns=["coordonnees_geo", "geometry"], inplace=True)

    return df


df_processed = preprocess_df(df)
display(df_processed.head())


id_trajectoire id_site                             label  \
0   10030_4 -> 2   10030  CF0001_9 boulevard de Sébastopol   
1   10030_2 -> 1   10030  CF0001_9 boulevard de Sébastopol   
2   10030_3 -> 2   10030  CF0001_9 boulevard de Sébastopol   
3   10030_1 -> 1   10030  CF0001_9 boulevard de Sébastopol   
4   10030_2 -> 1   10030  CF0001_9 boulevard de Sébastopol   

                          t          mode  nb_usagers  \
0 2024-03-15 03:00:00+00:00  Trottinettes           4   
1 2024-07-24 09:00:00+00:00         Vélos          12   
2 2024-06-03 05:00:00+00:00  Trottinettes          32   
3 2024-06-01 17:00:00+00:00         Vélos          26   
4 2023-11-10 18:00:00+00:00         Vélos          16   

                           voie sens trajectoire                   t_paris  \
0                Piste cyclable  N-S      4 -> 2 2024-03-15 04:00:00+01:00   
1  Voie de circulation générale  S-N      2 -> 1 2024-07-24 11:00:00+02:00   
2                Piste cyclable  S-N      3 -> 2 2024-06-03 07:00:00+02:00   
3  Voie de circulation générale  S-N      1 -> 1 2024-06-01 19:00:00+02:00   
4  Voie de circulation générale  S-N      2 -> 1 2023-11-10 19:00:00+01:00   

         date       lon        lat  
0  2024-03-15  2.348208  48.858628  
1  2024-07-24  2.348208  48.858628  
2  2024-06-03  2.348208  48.858628  
3  2024-06-01  2.348208  48.858628  
4  2023-11-10  2.348208  48.858628

# plot sites location 

In [203]:
def plot_sites_location(df: pd.DataFrame) -> go.Figure:
    """
    Creates a Plotly scatter map to display the locations of counting sites.
    """
    fig = go.Figure(
        go.Scattermap(
            lat=df["lat"],
            lon=df["lon"],
            mode="markers+text",
            marker=dict(size=14, symbol="marker"),
            text=df["label"] + " (" + df["id_site"] + ")",
            textposition="top right",
            textfont=dict(size=12, color="black"),
        )
    )

    # Configure map layout
    fig.update_layout(
        map=dict(
            center=dict(lat=df["lat"].mean(), lon=df["lon"].mean()),
            zoom=13.75,
        ),
        showlegend=False,
        margin=dict(l=30, r=30, t=50, b=30),
        title="Locations of Counting Sites",
        height=400,
        width=800,
    )

    return fig


In [204]:
df_map_plot = df_processed[["id_site", "label", "lon", "lat"]].drop_duplicates()
plot_sites_location(df_map_plot).show()

# Hourly Bike and Scooter Count

In [205]:
def plot_multimodal_site(df: pd.DataFrame, site_id: str) -> px.line:
    """
    Plots hourly multimodal counts at a given site
    """
    # 1) Filter to the specified site
    df_site = df[df["id_site"] == site_id].copy()

    # 2) Resample to an hourly grid for each transport mode
    df_resampled = (
        df_site.set_index("t_paris")
        .groupby("mode")["nb_usagers"]
        .resample("h")
        .sum()
        .reset_index()
    )

    # 3) Create the line plot
    fig = px.line(
        df_resampled,
        x="t_paris",
        y="nb_usagers",
        color="mode",
        title=f"Multimodal Hourly Count – Site {site_id}",
        labels={
            "t_paris": "Date and Time",
            "nb_usagers": "Number of Users",
            "mode": "Transport Mode",
        },
    )

    return fig


In [206]:
df_plot = (
    df_processed.groupby(["id_site", "t_paris", "mode"])["nb_usagers"]
    .sum()
    .reset_index()
)
display(df_plot.head())

# Display the chart for each site
for site in df_processed["id_site"].unique():
    plot_multimodal_site(df_processed, site).show()

id_site                   t_paris          mode  nb_usagers
0   10030 2021-06-04 17:00:00+02:00  Trottinettes          47
1   10030 2021-06-04 17:00:00+02:00         Vélos         873
2   10030 2021-06-04 18:00:00+02:00  Trottinettes          66
3   10030 2021-06-04 18:00:00+02:00         Vélos        1313
4   10030 2021-06-04 19:00:00+02:00  Trottinettes          64

## Identify missing data or gaps

In [216]:
print(f"Number of zero counts {(df_processed['nb_usagers'] == 0).sum()}")
display(df_processed[df_processed["date"] == "2024-07-04"])
display(df_processed[df_processed["date"] == "2024-10-20"])


Number of zero counts 0


Empty DataFrame
Columns: [id_trajectoire, id_site, label, t, mode, nb_usagers, voie, sens, trajectoire, t_paris, date, lon, lat]
Index: []

Empty DataFrame
Columns: [id_trajectoire, id_site, label, t, mode, nb_usagers, voie, sens, trajectoire, t_paris, date, lon, lat]
Index: []

# Focus - Site 10030 - Bike

## Date Aggregation

In [365]:
df_scope = (
    df_processed.query("id_site=='10030' and mode=='Vélos'")
    .set_index("t_paris")["nb_usagers"] 
    .resample("h")
    .sum(min_count=1)  # hours with no data will be NaN
    .to_frame()
)

## Highlight missing data

In [367]:
def summarize_missing_by_month(df_scope: pd.DataFrame) -> pd.DataFrame:
    """
    Compute, for each past calendar month (excluding the current month),
    the number of missing hourly slots, total theoretical hours, and
    percentage missing—only for months with at least one missing hour.
    """
    # 1) Count missing and total hours per month (MS = month start)
    missing = df_scope["nb_usagers"].isna().resample("MS").sum()
    total   = df_scope["nb_usagers"].resample("MS").size()

    summary = pd.DataFrame({
        "missing_hours": missing,
        "total_hours":   total
    })
    summary["pct_missing"] = summary["missing_hours"] / summary["total_hours"] * 100

    # 2) Keep only months with at least one missing hour
    summary = summary[summary["missing_hours"] > 0]

    # 3) Exclude the current month
    current_month = pd.Timestamp.now().to_period("M")
    # Convert summary index (DatetimeIndex at MS) to PeriodIndex
    period_index = summary.index.tz_localize(None).to_period("M")
    # Filter out current month
    summary = summary[period_index != current_month]

    # 4) Reassign clean PeriodIndex
    summary.index = period_index[period_index != current_month]
    summary.index.name = "month"

    return summary

In [368]:
df_periods = summarize_missing_by_month(df_scope)
display(df_periods)

missing_hours  total_hours  pct_missing
month                                           
2021-10              1          745     0.134228
2021-11             24          720     3.333333
2021-12             24          744     3.225806
2022-01             24          744     3.225806
2022-02             72          672    10.714286
2022-07            144          744    19.354839
2022-08            120          744    16.129032
2022-09             72          720    10.000000
2022-10            217          745    29.127517
2022-11            216          720    30.000000
2022-12            192          744    25.806452
2023-01            120          744    16.129032
2023-02             24          672     3.571429
2023-03            144          743    19.380888
2023-04            120          720    16.666667
2023-05            192          744    25.806452
2023-06             24          720     3.333333
2023-07             34          744     4.569892
2023-08             48          744     6.451613
2023-09            120          720    16.666667
2023-10            107          745    14.362416
2023-11            288          720    40.000000
2023-12            408          744    54.838710
2024-01             72          744     9.677419
2024-03              1          743     0.134590
2024-04             24          720     3.333333
2024-05            192          744    25.806452
2024-06            312          720    43.333333
2024-07            216          744    29.032258
2024-08            206          744    27.688172
2024-09            691          720    95.972222
2024-10            745          745   100.000000
2024-11            720          720   100.000000
2024-12            744          744   100.000000
2025-01            744          744   100.000000
2025-02            504          672    75.000000
2025-03             67          743     9.017497
2025-04             24          720     3.333333
2025-05             24          744     3.225806
2025-06              2          720     0.277778

## Impute missing data

In [404]:
df_imputed = df_scope.interpolate(method='time')
assert df_imputed.isna().sum().sum() == 0

## Aggregated counts + average profiles

In [386]:
def plot_aggregated_counts(df: pd.DataFrame) -> go.Figure:
    """
    Creates an interactive Plotly figure with buttons to display
    aggregated user counts at hourly, daily, and monthly levels.
    """
    # Aggregate by frequency
    df_hour = df['nb_usagers'].resample("h").sum().reset_index()
    df_day = df["nb_usagers"].resample("d").sum().reset_index()
    df_month = df["nb_usagers"].resample("MS").sum().reset_index()

    # Traces
    trace_hour = go.Scatter(
        x=df_hour['t_paris'], y=df_hour["nb_usagers"], name="Hourly", visible=True
    )
    trace_day = go.Scatter(
        x=df_day['t_paris'], y=df_day["nb_usagers"], name="Daily", visible=False
    )
    trace_month = go.Scatter(
        x=df_month['t_paris'], y=df_month["nb_usagers"], name="Monthly", visible=False
    )

    # Buttons
    buttons = [
        dict(
            label="Hourly",
            method="update",
            args=[
                {"visible": [True, False, False]},
                {
                    "title": "Hourly Counts",
                    "xaxis": {"title": "Date / Time"},
                },
            ],
        ),
        dict(
            label="Daily",
            method="update",
            args=[
                {"visible": [False, True, False]},
                {
                    "title": "Daily Counts",
                    "xaxis": {"title": "Date"},
                },
            ],
        ),
        dict(
            label="Monthly",
            method="update",
            args=[
                {"visible": [False, False, True]},
                {
                    "title": "Monthly Counts",
                    "xaxis": {"title": "Month"},
                },
            ],
        ),
    ]

    fig = go.Figure(data=[trace_hour, trace_day, trace_month])
    fig.update_layout(
        updatemenus=[
            dict(
                type="buttons",
                direction="right",
                x=0.5,
                y=1.15,
                showactive=True,
                buttons=buttons,
            )
        ],
        title="Hourly Counts",
        yaxis_title="Number of Users",
        xaxis=dict(type="date", title="Date / Time"),
    )

    return fig

In [375]:
def plot_average_profiles(df: pd.DataFrame) -> go.Figure:
    """
    Creates an interactive Plotly figure with buttons to visualize
    the average usage profiles by hour of day, weekday, and month.
    """
    # 1) Average by hour of the day (0–23)
    hourly_sum = df['nb_usagers'].resample("h").sum()
    df_hour = (
        hourly_sum.groupby(hourly_sum.index.hour)
        .mean()
        .rename_axis("hour")
        .reset_index(name="nb_usagers")
    )

    # 2) Average daily total by weekday
    daily_sum = df["nb_usagers"].resample("d").sum()
    df_wd = (
        daily_sum.groupby(daily_sum.index.weekday)
        .mean()
        .rename_axis("weekday")
        .reset_index(name="nb_usagers")
    )
    df_wd["weekday_name"] = df_wd["weekday"].map(
        {i: name for i, name in enumerate(calendar.day_name)}
    )

    # 3) Average by month of the year
    monthly_sum = df["nb_usagers"].resample("MS").sum()
    df_mo = (
        monthly_sum.groupby(monthly_sum.index.month)
        .mean()
        .rename_axis("month")
        .reset_index(name="nb_usagers")
    )
    df_mo["month_name"] = df_mo["month"].map(
        {i: calendar.month_name[i] for i in range(1, 13)}
    )

    # --- Traces with markers ---
    trace_hour = go.Scatter(
        x=df_hour["hour"],
        y=df_hour["nb_usagers"],
        mode="lines+markers",
        marker=dict(symbol="circle", size=6),
        name="Hourly",
        visible=True,
    )
    trace_wd = go.Scatter(
        x=df_wd["weekday_name"],
        y=df_wd["nb_usagers"],
        mode="lines+markers",
        marker=dict(symbol="square", size=6),
        name="By Weekday",
        visible=False,
    )
    trace_mo = go.Scatter(
        x=df_mo["month_name"],
        y=df_mo["nb_usagers"],
        mode="lines+markers",
        marker=dict(symbol="diamond", size=6),
        name="By Month",
        visible=False,
    )

    # Buttons in order: Hourly, By Weekday, By Month
    buttons = [
        dict(
            label="Hourly",
            method="update",
            args=[
                {"visible": [True, False, False]},
                {
                    "title": "Average Usage by Hour",
                    "xaxis": {"title": "Hour of Day (0–23)"},
                    "yaxis": {"title": "Average Number of Users"},
                },
            ],
        ),
        dict(
            label="By Weekday",
            method="update",
            args=[
                {"visible": [False, True, False]},
                {
                    "title": "Average Daily Total by Weekday",
                    "xaxis": {"title": "Weekday"},
                    "yaxis": {"title": "Average Number of Users"},
                },
            ],
        ),
        dict(
            label="By Month",
            method="update",
            args=[
                {"visible": [False, False, True]},
                {
                    "title": "Average Usage by Month",
                    "xaxis": {"title": "Month of Year"},
                    "yaxis": {"title": "Average Number of Users"},
                },
            ],
        ),
    ]

    fig = go.Figure(data=[trace_hour, trace_wd, trace_mo])
    fig.update_layout(
        updatemenus=[
            dict(
                type="buttons",
                direction="right",
                x=0.5,
                y=1.15,
                showactive=True,
                buttons=buttons,
            )
        ],
        title="Average Usage by Hour",
        yaxis_title="Average Number of Users",
        xaxis_title="Hour of Day (0–23)",
    )

    return fig


In [396]:
plot_aggregated_counts(df_imputed.loc[:"2024-08-31"]).show()

In [397]:
plot_average_profiles(df_imputed.loc[:"2024-08-31"]).show()

# MSTL decomposition

In [ ]:
# Select the series
s = df_imputed.loc['2023-01-01':'2023-12-31']

# Instantiate and fit MSTL
mstl = MSTL(
    s,
    periods=[24, 24*7], # daily and weekly
)
res = mstl.fit()


In [ ]:
# Extract components
obs      = res.observed
trend    = res.trend
seasonal = res.seasonal      # DataFrame with seasonal_24 & seasonal_168
resid    = res.resid

# Plot with Plotly
fig = make_subplots(
    rows=5, cols=1, shared_xaxes=True,
    vertical_spacing=0.02,
    subplot_titles=[
        "Observed",
        "Trend",
        "Daily Seasonality (24h)",
        "Weekly Seasonality (168h)",
        "Residual"
    ]
)

fig.add_trace(
    go.Scatter(x=obs.index, y=obs, name="Observed"),
    row=1, col=1
)
fig.add_trace(
    go.Scatter(x=trend.index, y=trend, name="Trend"),
    row=2, col=1
)
fig.add_trace(
    go.Scatter(x=seasonal.index, y=seasonal["seasonal_24"], name="Daily"),
    row=3, col=1
)
fig.add_trace(
    go.Scatter(x=seasonal.index, y=seasonal["seasonal_168"], name="Weekly"),
    row=4, col=1
)
# Residual as scatter markers
fig.add_trace(
    go.Scatter(
        x=resid.index,
        y=resid,
        mode="markers",
        marker=dict(symbol="circle", size=4),
        name="Residual"
    ),
    row=5, col=1
)

fig.update_layout(
    height=800,
    title_text="MSTL Decomposition (2023)",
    showlegend=False
)

fig.show()
